In [1]:
from seeq import spy
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import solara
import os
import urllib.parse as urlparse
from urllib.parse import parse_qs
from requests.models import PreparedRequest

In [19]:
def generate_chart(df=None, signal_map=None, jitter=1, whiskerwidth=1, show_box_points=False, title=None, height=500, width=1200):
    """
    Generate a box plot chart using Plotly.

    Args:
        df (pandas.DataFrame): A DataFrame containing the data to be plotted.
        signal_map (dict): A dictionary mapping column names to dictionaries containing asset, name, and color information.
        jitter (float, optional): The amount of jitter to apply to the box points. Defaults to 1.
        whiskerwidth (float, optional): The width of the whiskers. Defaults to 1.
        show_box_points (bool, optional): Whether to show individual box points. Defaults to False.
        title (str, optional): The title of the chart. Defaults to None.
        height (int, optional): The height of the chart in pixels. Defaults to 500.

    Returns:
        plotly.graph_objects.Figure: A Plotly figure object containing the box plot chart.
    """
    
    # Create a figure object once and update it
    fig = go.Figure()

    # Use a list comprehension to create traces efficiently
    traces = [
        go.Box(
            y=series,
            name=f"{signal_map[name]['Asset']} >> {signal_map[name]['Name']}",
            marker_color=signal_map[name]["Color"],
            boxmean="sd",
            boxpoints='all' if show_box_points else None,
            jitter=jitter,
            whiskerwidth=whiskerwidth
        )
        for name, series in df.items()
    ]

    # Add traces to the figure object
    fig.add_traces(traces)

    # Update layout properties
    fig.update_layout(
        title=title,
        height=height,
        width=width,
        # autosize=True,
        showlegend=False,
    )
    fig.update_annotations(
        font=dict(family="Helvetica", size=12),
        xanchor='left',
        x=0.0
                          )

    return fig

In [20]:
def parse_jupyter_notebook_url(jupyter_notebook_url, backup_workbench):
    """
    Parses the Jupyter Notebook URL and returns the workbook ID and worksheet ID.

    Args:
        jupyter_notebook_url (str): The URL of the Jupyter Notebook.
        backup_workbench (str): The URL of a backup Seeq Worksheet with signals in the details pane.

    Returns:
        tuple: A tuple containing the workbook ID and worksheet ID.
    """
    parsed_url = urlparse.urlparse(jupyter_notebook_url)
    query_params = parse_qs(parsed_url.query)

    if not query_params:
        # Assuming it's not being run as an Add-on and there are no query parameters
        # Manually including defaults from the backup_workbench
        url = spy.utils.get_data_lab_project_url()
        workbook_id = spy.utils.get_workbook_id_from_url(backup_workbench)
        worksheet_id = spy.utils.get_worksheet_id_from_url(backup_workbench)
        params = {'workbookId': workbook_id, 'worksheetId': worksheet_id}
        req = PreparedRequest()
        req.prepare_url(url, params)
        parsed_url = urlparse.urlparse(req.url)
        query_params = parse_qs(parsed_url.query)

    workbook_id = query_params['workbookId'][0]
    worksheet_id = query_params['worksheetId'][0]

    return workbook_id, worksheet_id

def create_df(workbook_id, worksheet_id):
    """
    Fetches worksheet data from a Seeq server and returns a DataFrame.

    Args:
        workbook_id (str): The ID of the workbook.
        worksheet_id (str): The ID of the worksheet.

    Returns:
        pandas.DataFrame: The fetched data DataFrame.
    """
    host = os.environ.get('SEEQ_HOST', spy.client.host[:-3])
    url = f"{host}workbook/{workbook_id}/worksheet/{worksheet_id}"

    # Fetch worksheet items and filter out string units of measure
    worksheet_items = spy.search(url, quiet=True)
    worksheet_items = worksheet_items[worksheet_items['Value Unit Of Measure'] != 'string']

    # Pull the workbook and specific worksheet
    workbook = spy.workbooks.pull(workbook_id,
                                  include_inventory=False,
                                  include_annotations=False,
                                  include_referenced_workbooks=False,
                                  include_images=False,
                                  include_rendered_content=False,
                                  specific_worksheet_ids=[worksheet_id],
                                  quiet=True)[0]

    worksheet = workbook.worksheets[0]

    # Update items to include the axis color
    display_items = worksheet.display_items[['ID', 'Color']]
    worksheet_items = pd.merge(worksheet_items, display_items, on='ID')

    # Get Display Range
    display_range = worksheet.display_range

    # Fetch data for the selected worksheet items
    df = spy.pull(worksheet_items,
                  start=display_range['Start'],
                  end=display_range['End'],
                  header="ID",
                  grid=None,
                  quiet=True)

    return df, worksheet_items

def signal_info_to_dict(worksheet_items):
    """
    Creates a signal map dictionary from the worksheet items.

    Args:
        worksheet_items (pandas.DataFrame): The worksheet items DataFrame.

    Returns:
        dict: The signal map dictionary.
    """
    signal_map = worksheet_items.set_index('ID').apply(lambda x: x.to_dict(), axis=1).to_dict()
    return signal_map

def get_worksheet_data(jupyter_notebook_url, backup_workbench):
    """
    Fetches worksheet data and signal map from a Seeq server based on the provided Jupyter Notebook URL.

    Args:
        jupyter_notebook_url (str): The URL of the Jupyter Notebook.
        backup_workbench (str): The URL of a backup Seeq Worksheet with signals in the details pane.

    Returns:
        tuple: A tuple containing the fetched data DataFrame and the signal map dictionary.
    """
    workbook_id, worksheet_id = parse_jupyter_notebook_url(jupyter_notebook_url, backup_workbench)
    df , worksheet_items= create_df(workbook_id, worksheet_id)
    signal_info = signal_info_to_dict(worksheet_items)

    return df, signal_info


In [21]:
@solara.component
def BoxPlotComponent():
    # State variables
    whisker_width, set_whisker_width = solara.use_state(1)
    show_data_points, set_show_data_points = solara.use_state(False)
    selected_jitter, set_jitter = solara.use_state(1)  
    error_message, set_error_message = solara.use_state(None)

    def validate_whisker_width(value):
        if value > 1:
            set_error_message("Whisker width cannot be greater than 1")
        else:
            set_error_message(None)
            set_whisker_width(value)

    def render_controls():
        with solara.HBox() as controls:
            solara.Select(
                label="Show Samples",
                values=[True, False],
                value=show_data_points,
                on_value=set_show_data_points,
            )

            if show_data_points:
                solara.Select(
                    label="Jitter",
                    values=[0, 0.1, 0.5, 1],
                    value=selected_jitter,
                    on_value=set_jitter,
                )

            solara.InputFloat(
                label="Whisker Width",
                value=whisker_width,
                on_value=validate_whisker_width,
            )

        return controls

    def render_chart():
        fig = generate_chart(
            df=df,
            jitter=selected_jitter,
            show_box_points=show_data_points,
            signal_map=signal_info,
            whiskerwidth=whisker_width,
            height=800,
            width=1200,
        )
        solara.FigurePlotly(fig, dependencies=[selected_jitter, show_data_points, whisker_width])

    with solara.Div() as main:
        with solara.AppBarTitle():
            solara.Text("Box Plot")

        if error_message:
            solara.Error(
                f"{error_message}",
                text=False,
                dense=True,
                outlined=False,
                icon=True,
            )

        render_controls()
        render_chart()

    return main


BoxPlotComponent()

Cannot show ipywidgets in text

In [ ]:
df, signal_info = get_worksheet_data(jupyter_notebook_url=jupyter_notebook_url)

# The following line is required when running the code in a Jupyter notebook:
BoxPlotComponent()